In [1]:
import numpy as np
import pandas as pd

In [2]:
ctes = pd.read_excel('ctes_final_new.xlsx') #Long data of patients, all the measurements and such
lab = pd.read_excel('laboratorio_final_new.xlsx') #Other, weirder long data?
pac = pd.read_excel('pac_covid.xlsx') #Patient basic info, ONE ROW PER PATIENT
pac["Dead"] = pac["fecha_fallece"].notna()


In [3]:
# ctes["Item__form_cte_"].unique()
# ctes["Item__form_cte_"].value_counts()
ctes["Etiqueta__form_cte_"].value_counts()


Etiqueta__form_cte_
presionarte    59107
saturaciono    50967
tiposaturac    48604
temperatura    43245
frecuenciac    33110
cantidadsat    29545
glucemia       19587
EscalaDolor    10452
frecuenciar     9099
espontanea      3919
deposicion      3134
PESO             159
TALLA             41
IMC               38
valorimc          37
Name: count, dtype: int64

In [4]:
# ctes[ctes["Etiqueta__form_cte_"]=="presionarte"]
ctes[ctes["Etiqueta__form_cte_"]=="valorimc"]["Valor__form_cte_"]

3403                    NaN
3472       Obesidad Grado I
4312     Obesidad Grado III
4568       Obesidad Grado I
4969              Normopeso
5106              Sobrepeso
5220              Sobrepeso
5351      Obesidad Grado II
5497     Obesidad Grado III
6548                    NaN
6761              Sobrepeso
6856              Normopeso
7131       Obesidad Grado I
7132              Sobrepeso
7137       Obesidad Grado I
7328              Normopeso
7329              Normopeso
8011              Normopeso
8012              Sobrepeso
8028              Sobrepeso
8899              Sobrepeso
9913              Normopeso
9914              Normopeso
10737             Normopeso
11057             Sobrepeso
11282     Peso Insuficiente
11301      Obesidad Grado I
11711             Sobrepeso
11927      Obesidad Grado I
12077             Normopeso
12163     Obesidad Grado II
12777             Sobrepeso
12795             Normopeso
13237      Obesidad Grado I
13493      Obesidad Grado I
13494             So

In [5]:
contVar = [
            "presionarte",
            "saturaciono",
            "temperatura",
            "frecuenciac",
            "glucemia",
            "frecuenciar",
            "espontanea",
            "PESO",
            "TALLA",
            "IMC"
        ]
catVar = [ 
            "tiposaturac",
            "cantidadsat",
            "EscalaDolor",
            "deposicion",
            "valorimc"
        ]

In [6]:
ctes["type"] = "cont"
for var in catVar:
    ctes.loc[ctes["Etiqueta__form_cte_"]==var,"type"] = "cat"

In [7]:
ctes["cont"] = -1 #so all non continous nums are ignored
for var in contVar:
    #really annoying formatting, but keep  it in mind for modifying dataframes downstream :/
    ctes.loc[ctes["Etiqueta__form_cte_"]==var,"cont"] = ctes[ctes["Etiqueta__form_cte_"]==var]["Valor__form_cte_"]

C:\Users\sergi\AppData\Local\Temp\ipykernel_460\701267067.py:4: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '['44' '48' '49' ... '97' '98' nan]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  ctes.loc[ctes["Etiqueta__form_cte_"]==var,"cont"] = ctes[ctes["Etiqueta__form_cte_"]==var]["Valor__form_cte_"]


In [8]:
ctes["cat"] = "NaN" #so all continous vars are ignored, keep in mind, NaN can also be imported from original Valor__form_cte_
for var in catVar:
    ctes.loc[ctes["Etiqueta__form_cte_"]==var,"cat"]= ctes[ctes["Etiqueta__form_cte_"]==var]["Valor__form_cte_"]

In [9]:
ctes[ctes["Etiqueta__form_cte_"]=="TALLA"].head()

Id_Paciente  Episodio___nico_    Tipo_episodio     Centro__episodio_  \
3404     45917537          68921463  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
3473     51000308          67775486  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
4313    196823679          68313851  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
4314    196823679          68313851  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
4569    215774911          67014111  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   

     Item__form_cte_ Valor__form_cte_  cod_Registro_Item__form_cte_  \
3404      talla (cm)              NaN                     454735868   
3473      talla (cm)              166                     395547484   
4313      talla (cm)             70,7                     422196744   
4314      talla (cm)             72,6                     422339988   
4569      talla (cm)              153                     360040298   

     Etiqueta__form_cte_ Fecha__form_cte_  hora  minuto  type  cont  cat  
3404               TALLA       2021-02-11    12      38  cont   NaN  NaN  
3473               TALLA       2020-09-15    14      29  cont   166  NaN  
4313               TALLA       2020-11-14    10      23  cont  70,7  NaN  
4314               TALLA       2020-11-15    11       0  cont  72,6  NaN  
4569               TALLA       2020-05-15    15       0  cont   153  NaN

In [10]:
pac[pac["Id_Paciente"]=="196823679"] #doesnt exist? need to clean/examine more closely, cuz this had 70cm height

Empty DataFrame
Columns: [Id_Paciente, Desc_Prueba, Fecha_validaci_n_prueba, Episodio___nico_, Sexo, Edad_a_os__actual_, Fecha__ingreso_, Fecha__alta_, fecha_fallece, dias_hasta_ingreso, dias_estancia, paso_uci, Dead]
Index: []

So, we want everything to be taped onto the edge of pac, the other two are long datasets

Ok, now let's try it for real with the full dataset

In [11]:
ctes2 = ctes.merge(
    pac[['Id_Paciente', 'Fecha__ingreso_']].drop_duplicates(),
    on='Id_Paciente',
    how='left'
)
ctes2["Days"] = ctes2["Fecha__form_cte_"]-ctes2["Fecha__ingreso_"]
ctes2["Days"]=ctes2["Days"].dt.days
ctes2

Id_Paciente  Episodio___nico_    Tipo_episodio     Centro__episodio_  \
0          14260524          66844681  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
1          14260524          66844681  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
2          14260524          66844681  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
3          14260524          66844681  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
4          14260524          66844681  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
...             ...               ...              ...                   ...   
311039   9307417479          66718266  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
311040   9307417479          66718266  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
311041   9307417479          66718266  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
311042   9307417479          66718266  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
311043   9307417479          66718266  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   

       Item__form_cte_ Valor__form_cte_  cod_Registro_Item__form_cte_  \
0           Deposición                1                     351290272   
1           Deposición                1                     351291772   
2           Deposición                1                     351305522   
3           Deposición                1                     351793519   
4           Deposición                1                     351949569   
...                ...              ...                           ...   
311039  Temperatura ºC             38.5                     347226116   
311040  Temperatura ºC             38.8                     344466722   
311041  Temperatura ºC             38.9                     344906359   
311042  Temperatura ºC             38.9                     346395071   
311043  Temperatura ºC             38.9                     346405172   

       Etiqueta__form_cte_ Fecha__form_cte_  hora  minuto  type  cont  cat  \
0               deposicion       2020-04-08     0      18   cat    -1    1   
1               deposicion       2020-04-08     0      31   cat    -1    1   
2               deposicion       2020-04-08     7       6   cat    -1    1   
3               deposicion       2020-04-09    21      33   cat    -1    1   
4               deposicion       2020-04-10    23      49   cat    -1    1   
...                    ...              ...   ...     ...   ...   ...  ...   
311039         temperatura       2020-03-23    22      26  cont  38.5  NaN   
311040         temperatura       2020-03-12     1      52  cont  38.8  NaN   
311041         temperatura       2020-03-13     2      32  cont  38.9  NaN   
311042         temperatura       2020-03-20     0      33  cont  38.9  NaN   
311043         temperatura       2020-03-20    20      49  cont  38.9  NaN   

       Fecha__ingreso_  Days  
0           2020-04-07     1  
1           2020-04-07     1  
2           2020-04-07     1  
3           2020-04-07     2  
4           2020-04-07     3  
...                ...   ...  
311039      2020-03-10    13  
311040      2020-03-10     2  
311041      2020-03-10     3  
311042      2020-03-10    10  
311043      2020-03-10    10  

[311044 rows x 16 columns]

In [12]:
ctes2["sumHour"] = ctes2["hora"]+(ctes2["Days"]*24)
ctes2

Id_Paciente  Episodio___nico_    Tipo_episodio     Centro__episodio_  \
0          14260524          66844681  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
1          14260524          66844681  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
2          14260524          66844681  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
3          14260524          66844681  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
4          14260524          66844681  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
...             ...               ...              ...                   ...   
311039   9307417479          66718266  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
311040   9307417479          66718266  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
311041   9307417479          66718266  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
311042   9307417479          66718266  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
311043   9307417479          66718266  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   

       Item__form_cte_ Valor__form_cte_  cod_Registro_Item__form_cte_  \
0           Deposición                1                     351290272   
1           Deposición                1                     351291772   
2           Deposición                1                     351305522   
3           Deposición                1                     351793519   
4           Deposición                1                     351949569   
...                ...              ...                           ...   
311039  Temperatura ºC             38.5                     347226116   
311040  Temperatura ºC             38.8                     344466722   
311041  Temperatura ºC             38.9                     344906359   
311042  Temperatura ºC             38.9                     346395071   
311043  Temperatura ºC             38.9                     346405172   

       Etiqueta__form_cte_ Fecha__form_cte_  hora  minuto  type  cont  cat  \
0               deposicion       2020-04-08     0      18   cat    -1    1   
1               deposicion       2020-04-08     0      31   cat    -1    1   
2               deposicion       2020-04-08     7       6   cat    -1    1   
3               deposicion       2020-04-09    21      33   cat    -1    1   
4               deposicion       2020-04-10    23      49   cat    -1    1   
...                    ...              ...   ...     ...   ...   ...  ...   
311039         temperatura       2020-03-23    22      26  cont  38.5  NaN   
311040         temperatura       2020-03-12     1      52  cont  38.8  NaN   
311041         temperatura       2020-03-13     2      32  cont  38.9  NaN   
311042         temperatura       2020-03-20     0      33  cont  38.9  NaN   
311043         temperatura       2020-03-20    20      49  cont  38.9  NaN   

       Fecha__ingreso_  Days  sumHour  
0           2020-04-07     1       24  
1           2020-04-07     1       24  
2           2020-04-07     1       31  
3           2020-04-07     2       69  
4           2020-04-07     3       95  
...                ...   ...      ...  
311039      2020-03-10    13      334  
311040      2020-03-10     2       49  
311041      2020-03-10     3       74  
311042      2020-03-10    10      240  
311043      2020-03-10    10      260  

[311044 rows x 17 columns]

In [13]:
# ctes2.loc[ctes2['Etiqueta__form_cte_']=="presionarte"]

# for patient in ctes2["Id_Paciente"].unique():
#     for hour in ctes2["Id_Paciente"].unique():



# # example original data update
# ctes.loc[ctes["Etiqueta__form_cte_"]==var,"cont"] = ctes[ctes["Etiqueta__form_cte_"]==var]["Valor__form_cte_"]

#scratchcode
# for every patient in patientID
#     For every unique number in sumHour
#         filter for presionarte
#         min value in valor = min
#         max value in valor = max
#         etiqueta where valor == min = Diastolic
#         etiqueta where valor == max = Systolic

In [14]:
# 9307417479
22329353
# df.loc[1:3, ['Name', 'Qualification']]
# ctes2[ctes2["Id_Paciente"]==9307417479].loc[:,["sumHour","Valor__form_cte_"]]
filter=np.where((ctes2['Id_Paciente']==22329353) & (ctes2['Etiqueta__form_cte_']=="presionarte"))
ctes2.loc[filter].loc[:,["sumHour","Valor__form_cte_"]]
# ctes2[    ctes2["Id_Paciente"]==22329353].loc[:,["sumHour","Valor__form_cte_"]]

# ctes2["Id_Paciente"]=="9307417479"
# ctes2[ctes2["Id_Paciente"]==9307417479]


sumHour Valor__form_cte_
208737      129               75
208738      202               75
208739      106               76
208740       20               78
208741      178               80
208742       34               81
208743       82               81
208744      154               84
208745       58               85
238258      202              130
238259       20              131
238260       82              146
238261      154              152
238262      178              160
238263      106              161
238264       34              163
238265      129              173
238266       58              176

In [15]:
# ctes.loc[ctes["Etiqueta__form_cte_"]==var,"cont"]
clean_ctes = []
i=0
for patient in ctes2["Id_Paciente"].unique():
    temp_ls = dict()
    min_hour = min(ctes2.loc[ctes2["Id_Paciente"]==patient]["sumHour"])
    max_hour = max(ctes2.loc[ctes2["Id_Paciente"]==patient]["sumHour"])    
    temp_ls["Id_Paciente"] = patient #to make leftmost col
    temp_ls["sumHour"] = list(range(min_hour,max_hour+1,1)) #+1 cuz range isn't last-inclusive
    temp_ls=pd.DataFrame.from_dict(temp_ls)
    temp_ls["Id_Paciente"] = patient #to fill
    
    for variable in ctes2["Etiqueta__form_cte_"].unique():
        filter=np.where((ctes2['Id_Paciente']==patient) & (ctes2['Etiqueta__form_cte_']==variable)) #gross but works great
        thinframe = ctes2.loc[filter].loc[:,["sumHour","Valor__form_cte_"]]
        temp_ls = pd.merge(temp_ls,thinframe,how='left',on=['sumHour'])
        temp_ls.rename({'Valor__form_cte_': variable}, axis='columns', inplace=True)

    #adjust to zero-standardize
    # max_hour=max_hour-min_hour
    # min_hour=0
    # temp_ls["sumHour"] = list(range(min_hour,max_hour+1,1)) #redeclare with adjusted values
    
    clean_ctes.append(temp_ls)
    i=i+1
    print(i/len(ctes2["Id_Paciente"].unique()))
        
# clean_ctes = pd.DataFrame(clean_ctes)


# So, lets draw out some scratch code
# collective_dataframe = df
# for each patient:
#     temporary_df = df    
#     min_hour = min(ctes2[patient][sumhour])
#     max_hour = max(ctes2[patient][sumhour])
#     temporarydf[sumhour] = range(minhour,maxhour,1) #makes the column be integer count of hours
#     temporarydf[id_pac] = patient #for easier joining later
#     for each Etiqueta__form_cte_ (variable):
#         join(tempdf,ctes2[variable][valor],on=sumHour)
    



0.0006090133982947625
0.001218026796589525
0.0018270401948842874
0.00243605359317905
0.0030450669914738123
0.0036540803897685747
0.004263093788063338
0.0048721071863581
0.0054811205846528625
0.0060901339829476245
0.006699147381242387
0.007308160779537149
0.007917174177831911
0.008526187576126675
0.009135200974421437
0.0097442143727162
0.010353227771010963
0.010962241169305725
0.011571254567600487
0.012180267965895249
0.012789281364190013
0.013398294762484775
0.014007308160779537
0.014616321559074299
0.015225334957369063
0.015834348355663823
0.016443361753958587
0.01705237515225335
0.01766138855054811
0.018270401948842874
0.018879415347137638
0.0194884287454324
0.020097442143727162
0.020706455542021926
0.021315468940316686
0.02192448233861145
0.02253349573690621
0.023142509135200974
0.023751522533495738
0.024360535931790498
0.024969549330085262
0.025578562728380026
0.026187576126674786
0.02679658952496955
0.027405602923264313
0.028014616321559074
0.028623629719853837
0.02923264311814859

In [ ]:
import copy
# backup = copy.deepcopy(clean_ctes)
clean_ctes = copy.deepcopy(backup)

In [17]:
#still need to hour standardize!!!!
clean_ctes[0]

Id_Paciente  sumHour deposicion EscalaDolor PESO  IMC valorimc TALLA  \
0       14260524       14        NaN         NaN  NaN  NaN      NaN   NaN   
1       14260524       14        NaN         NaN  NaN  NaN      NaN   NaN   
2       14260524       15        NaN         NaN  NaN  NaN      NaN   NaN   
3       14260524       16        NaN         NaN  NaN  NaN      NaN   NaN   
4       14260524       17        NaN         NaN  NaN  NaN      NaN   NaN   
..           ...      ...        ...         ...  ...  ...      ...   ...   
334     14260524      246        NaN         NaN  NaN  NaN      NaN   NaN   
335     14260524      247        NaN         NaN  NaN  NaN      NaN   NaN   
336     14260524      248        NaN         NaN  NaN  NaN      NaN   NaN   
337     14260524      249        NaN         NaN  NaN  NaN      NaN   NaN   
338     14260524      249        NaN         NaN  NaN  NaN      NaN   NaN   

    cantidadsat saturaciono tiposaturac espontanea frecuenciac frecuenciar  \
0          0,35          96         VMK        NaN         110         NaN   
1          0,35          96         VMK        NaN         110         NaN   
2           NaN         NaN         NaN        NaN         NaN         NaN   
3           NaN         NaN         NaN        NaN         NaN         NaN   
4          0,35          97         VMK        NaN         110         NaN   
..          ...         ...         ...        ...         ...         ...   
334         NaN         NaN         NaN        NaN         NaN         NaN   
335         NaN         NaN         NaN        NaN         NaN         NaN   
336         NaN         NaN         NaN        NaN         NaN         NaN   
337          2L          95     GafasO2        NaN         100         NaN   
338          2L          95     GafasO2        NaN         100         NaN   

    glucemia presionarte temperatura  
0        NaN          79        37.2  
1        NaN         144        37.2  
2        NaN         NaN         NaN  
3        NaN         NaN         NaN  
4        NaN         NaN        37.8  
..       ...         ...         ...  
334      NaN         NaN         NaN  
335      NaN         NaN         NaN  
336      NaN         NaN         NaN  
337      NaN          84        36.9  
338      NaN         130        36.9  

[339 rows x 17 columns]

In [18]:
clean_ctes[0]["saturaciono"]

0       96
1       96
2      NaN
3      NaN
4       97
      ... 
334    NaN
335    NaN
336    NaN
337     95
338     95
Name: saturaciono, Length: 339, dtype: object

In [27]:
clean_ctes[0].dtypes
# dtype('O') means string because we don't know how to make things easy i guess


Id_Paciente     int64
sumHour         int64
deposicion     object
EscalaDolor    object
PESO           object
IMC            object
valorimc       object
TALLA          object
cantidadsat    object
saturaciono    object
tiposaturac    object
espontanea     object
frecuenciac    object
frecuenciar    object
glucemia       object
presionarte    object
temperatura    object
dtype: object

In [ ]:
#TYPESETTING
#I'm just gonna get rid of cantidadsat, deadass it makes no sense and sucks
# convert all the categorical stuff to categorical format and numbers from string to int or float
#lets start by converting to numbers
for table in clean_ctes:
    for label in contVar:
        #first, check if its a string

        #if it is a string, then replace commas with points
        table[label] = table[label].str.replace(',', '.')

        #then, check if it can be converted to numeric
        #if it can be, do so

        # table[label] = table[label].str.replace(',', '.')
        # table[label] = [y.replace(',','.') for y in table[label]]
        # table[label] = pd.to_numeric(table[label])

0       79
1      144
2      NaN
3      NaN
4      NaN
      ... 
334    NaN
335    NaN
336    NaN
337     84
338    130
Name: presionarte, Length: 339, dtype: object
0       96
1       96
2      NaN
3      NaN
4       97
      ... 
334    NaN
335    NaN
336    NaN
337     95
338     95
Name: saturaciono, Length: 339, dtype: object
0      37.2
1      37.2
2       NaN
3       NaN
4      37.8
       ... 
334     NaN
335     NaN
336     NaN
337    36.9
338    36.9
Name: temperatura, Length: 339, dtype: object
0      110
1      110
2      NaN
3      NaN
4      110
      ... 
334    NaN
335    NaN
336    NaN
337    100
338    100
Name: frecuenciac, Length: 339, dtype: object
0      NaN
1      NaN
2      NaN
3      NaN
4      NaN
      ... 
334    NaN
335    NaN
336    NaN
337    NaN
338    NaN
Name: glucemia, Length: 339, dtype: object
0      NaN
1      NaN
2      NaN
3      NaN
4      NaN
      ... 
334    NaN
335    NaN
336    NaN
337    NaN
338    NaN
Name: frecuenciar, Length: 339, dtyp

In [37]:
clean_ctes[0]["cantidadsat"]

0      0,35
1      0,35
2       NaN
3       NaN
4      0,35
       ... 
334     NaN
335     NaN
336     NaN
337      2L
338      2L
Name: cantidadsat, Length: 339, dtype: object

In [109]:
#make minitables from each of the one variable tables here and then stitch them together later
# clean_ctes[0]
# max(clean_ctes[0]["presionarte"])
type(clean_ctes[0]["presionarte"][1])

str

In [ ]:
# filter=np.where((ctes2['Id_Paciente']==patient) & (ctes2['Etiqueta__form_cte_']==variable)) #gross but works great
# thinframe = ctes2.loc[filter].loc[:,["sumHour","Valor__form_cte_"]]

for table in clean_ctes:
    #check if sumhour filtered minitable has 2 or more rows, meaning it has the presionarte variable in it and isnt empty row
    for hour in table["sumHour"].unique():
        if len(table[table["sumHour"]==hour]) >= 2: #if this hour has at least 2 rows
            table["sysPres"] = max(table["presionarte"])
            table["diasPres"] = min(table["presionarte"])

TypeError: cannot convert the series to <class 'int'>

In [38]:
clean=pd.concat(clean_ctes) #not really necessary, i think, since we can make the summary_tables from the isolated ones in clean_ctes methinks?

In [40]:
clean_ctes[0].to_excel("clean.xlsx")  

In [91]:
clean

Id_Paciente  sumHour deposicion EscalaDolor PESO  IMC valorimc TALLA  \
0      14260524       14        NaN         NaN  NaN  NaN      NaN   NaN   
1      14260524       14        NaN         NaN  NaN  NaN      NaN   NaN   
2      14260524       15        NaN         NaN  NaN  NaN      NaN   NaN   
3      14260524       16        NaN         NaN  NaN  NaN      NaN   NaN   
4      14260524       17        NaN         NaN  NaN  NaN      NaN   NaN   
..          ...      ...        ...         ...  ...  ...      ...   ...   
1    1350497737       20        NaN         NaN  NaN  NaN      NaN   NaN   
2    1350497737       21        NaN         NaN  NaN  NaN      NaN   NaN   
3    1350497737       21        NaN         NaN  NaN  NaN      NaN   NaN   
0    1382153208       15        NaN         NaN  NaN  NaN      NaN   NaN   
1    1382153208       15        NaN         NaN  NaN  NaN      NaN   NaN   

   cantidadsat saturaciono tiposaturac espontanea frecuenciac frecuenciar  \
0         0,35          96         VMK        NaN         110         NaN   
1         0,35          96         VMK        NaN         110         NaN   
2          NaN         NaN         NaN        NaN         NaN         NaN   
3          NaN         NaN         NaN        NaN         NaN         NaN   
4         0,35          97         VMK        NaN         110         NaN   
..         ...         ...         ...        ...         ...         ...   
1          NaN         NaN         NaN        NaN          71         NaN   
2          NaN         NaN         NaN        NaN         NaN         NaN   
3          NaN         NaN         NaN        NaN         NaN         NaN   
0          NaN         NaN         NaN        NaN          79         NaN   
1          NaN         NaN         NaN        NaN          79         NaN   

   glucemia presionarte temperatura  
0       NaN          79        37.2  
1       NaN         144        37.2  
2       NaN         NaN         NaN  
3       NaN         NaN         NaN  
4       NaN         NaN        37.8  
..      ...         ...         ...  
1       NaN         139        36.6  
2       NaN          79          37  
3       NaN         135          37  
0       NaN          72          37  
1       NaN         130          37  

[23325618 rows x 17 columns]

In [93]:
23957137
ctes2.loc[ctes2["Id_Paciente"]==23957137].sort_values(by=['sumHour'])

Id_Paciente  Episodio___nico_    Tipo_episodio     Centro__episodio_  \
3141       23957137          68731843  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
14217      23957137          68731843  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
14249      23957137          68731843  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
14259      23957137          68731843  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
147011     23957137          68731843  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
...             ...               ...              ...                   ...   
267921     23957137          68731843  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
14285      23957137          68731843  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
14230      23957137          68731843  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
3154       23957137          68731843  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   
267922     23957137          68731843  HOSPITALIZACIÓN  H. GALDAKAO-USANSOLO   

        Item__form_cte_ Valor__form_cte_  cod_Registro_Item__form_cte_  \
3141    Escala de dolor     No dolor - 0                     442965548   
14217   Cantidad de Sat               2L                     442965547   
14249   Saturación capi               97                     442965545   
14259   Tipo de Saturac          GafasO2                     442965546   
147011  Frecuencia Card               86                     442965544   
...                 ...              ...                           ...   
267921   Temperatura ºC             37.4                     445915570   
14285   Tipo de Saturac         Optiflow                     446032297   
14230   Saturación capi               82                     446032296   
3154    Escala de dolor     No valorable                     446032299   
267922   Temperatura ºC             37.8                     446032294   

       Etiqueta__form_cte_ Fecha__form_cte_  hora  minuto  type  cont  \
3141           EscalaDolor       2021-01-13    18      24   cat    -1   
14217          cantidadsat       2021-01-13    18      24   cat    -1   
14249          saturaciono       2021-01-13    18      24  cont    97   
14259          tiposaturac       2021-01-13    18      24   cat    -1   
147011         frecuenciac       2021-01-13    18      24  cont    86   
...                    ...              ...   ...     ...   ...   ...   
267921         temperatura       2021-01-21     1       9  cont  37.4   
14285          tiposaturac       2021-01-21     9      58   cat    -1   
14230          saturaciono       2021-01-21     9      58  cont    82   
3154           EscalaDolor       2021-01-21     9      58   cat    -1   
267922         temperatura       2021-01-21     9      58  cont  37.8   

                 cat Fecha__ingreso_  Days  sumHour  
3141    No dolor - 0      2021-01-13     0       18  
14217             2L      2021-01-13     0       18  
14249            NaN      2021-01-13     0       18  
14259        GafasO2      2021-01-13     0       18  
147011           NaN      2021-01-13     0       18  
...              ...             ...   ...      ...  
267921           NaN      2021-01-13     8      193  
14285       Optiflow      2021-01-13     8      201  
14230            NaN      2021-01-13     8      201  
3154    No valorable      2021-01-13     8      201  
267922           NaN      2021-01-13     8      201  

[189 rows x 17 columns]

In [12]:
ctes_pivot = pd.pivot_table(ctes2,
               values="Valor__form_cte_",
               index="Id_Paciente",
               columns=["Etiqueta__form_cte_","Days","hora"],
               aggfunc="first")

Maybe we should standardize the times here before we go on to stitch them together, so instead of Measurement_Date_Hour_Minute, its standardized to be How much time since entry, or even just to only how many hours since, and we keep it to that.

In [13]:
ctes_pivot.columns = ctes_pivot.columns.to_flat_index()  # Converts MultiIndex to tuples
# ctes_pivot.columns = ['_'.join(col) for col in ctes_pivot.columns]  # Join tuples
ctes_pivot

(EscalaDolor, 0 days 00:00:00, 0)  \
Id_Paciente                                     
11711053                                  NaN   
14260524                                  NaN   
14409908                                  NaN   
22329353                                  NaN   
23608324                                  NaN   
...                                       ...   
9245104453                                NaN   
9278045053                                NaN   
9283692237                                NaN   
9294732495                                NaN   
9307417479                                NaN   

            (EscalaDolor, 0 days 00:00:00, 1)  \
Id_Paciente                                     
11711053                                  NaN   
14260524                                  NaN   
14409908                                  NaN   
22329353                                  NaN   
23608324                                  NaN   
...                                       ...   
9245104453                                NaN   
9278045053                                NaN   
9283692237                                NaN   
9294732495                                NaN   
9307417479                                NaN   

            (EscalaDolor, 0 days 00:00:00, 2)  \
Id_Paciente                                     
11711053                                  NaN   
14260524                                  NaN   
14409908                                  NaN   
22329353                                  NaN   
23608324                                  NaN   
...                                       ...   
9245104453                                NaN   
9278045053                                NaN   
9283692237                                NaN   
9294732495                                NaN   
9307417479                                NaN   

            (EscalaDolor, 0 days 00:00:00, 3)  \
Id_Paciente                                     
11711053                                  NaN   
14260524                                  NaN   
14409908                                  NaN   
22329353                                  NaN   
23608324                                  NaN   
...                                       ...   
9245104453                                NaN   
9278045053                                NaN   
9283692237                                NaN   
9294732495                     Dolor leve - 2   
9307417479                                NaN   

            (EscalaDolor, 0 days 00:00:00, 4)  \
Id_Paciente                                     
11711053                                  NaN   
14260524                                  NaN   
14409908                                  NaN   
22329353                                  NaN   
23608324                                  NaN   
...                                       ...   
9245104453                                NaN   
9278045053                                NaN   
9283692237                                NaN   
9294732495                                NaN   
9307417479                                NaN   

            (EscalaDolor, 0 days 00:00:00, 5)  \
Id_Paciente                                     
11711053                                  NaN   
14260524                                  NaN   
14409908                                  NaN   
22329353                                  NaN   
23608324                                  NaN   
...                                       ...   
9245104453                                NaN   
9278045053                                NaN   
9283692237                                NaN   
9294732495                                NaN   
9307417479                                NaN   

            (EscalaDolor, 0 days 00:00:00, 6)  \
Id_Paciente                                     
11711053                                  NaN   
14260524                             

In [16]:
joined_1 = pac.join(ctes_pivot, on="Id_Paciente", how="left")
joined_1

Id_Paciente                  Desc_Prueba Fecha_validaci_n_prueba  \
0        11711053  Coronavirus 2019-nCoV (ARN)              2020-03-16   
1        14260524  Coronavirus 2019-nCoV (ARN)              2020-04-07   
2        14409908  Coronavirus 2019-nCoV (ARN)              2020-03-31   
3        22329353  Coronavirus 2019-nCoV (ARN)              2020-09-24   
4        23608324  Coronavirus 2019-nCoV (ARN)              2020-03-13   
...           ...                          ...                     ...   
1637   9245104453  Coronavirus 2019-nCoV (ARN)              2021-04-13   
1638   9278045053  Coronavirus 2019-nCoV (ARN)              2020-03-23   
1639   9283692237  Coronavirus-SARS-2 Ag (ICT)              2021-01-06   
1640   9294732495  Coronavirus 2019-nCoV (ARN)              2021-01-19   
1641   9307417479  Coronavirus 2019-nCoV (ARN)              2020-03-10   

      Episodio___nico_    Sexo  Edad_a_os__actual_ Fecha__ingreso_  \
0             66755125  Hombre                  86      2020-03-16   
1             66844681   Mujer                  97      2020-04-07   
2             66822847   Mujer                  94      2020-04-01   
3             67973760   Mujer                  91      2020-10-01   
4             66745194  Hombre                  90      2020-03-13   
...                ...     ...                 ...             ...   
1637          69499309   Mujer                  50      2021-04-17   
1638          66783136   Mujer                  34      2020-03-23   
1639          68713110   Mujer                  63      2021-01-12   
1640          68769742   Mujer                  32      2021-01-19   
1641          66718266  Hombre                  50      2020-03-10   

     Fecha__alta_ fecha_fallece  dias_hasta_ingreso  ...  \
0      2020-03-21    2020-03-21                   0  ...   
1      2020-04-17           NaT                   0  ...   
2      2020-04-04    2020-04-04                   1  ...   
3      2020-10-09           NaT                   7  ...   
4      2020-03-21           NaT                   0  ...   
...           ...           ...                 ...  ...   
1637   2021-04-20           NaT                   4  ...   
1638   2020-03-26           NaT                   0  ...   
1639   2021-01-19           NaT                   6  ...   
1640   2021-01-20           NaT                   0  ...   
1641   2020-04-17           NaT                   0  ...   

      (talla (cm), 24 days 00:00:00, 13)  (talla (cm), 25 days 00:00:00, 19)  \
0                                    NaN                                 NaN   
1                                    NaN                                 NaN   
2                                    NaN                                 NaN   
3                                    NaN                                 NaN   
4                                    NaN                                 NaN   
...                                  ...                                 ...   
1637                                 NaN                                 NaN   
1638                                 NaN                                 NaN   
1639                                 NaN                                 NaN   
1640                                 NaN                                 NaN   
1641                                 NaN                                 NaN   

      (talla (cm), 25 days 00:00:00, 20) (talla (cm), 28 days 00:00:00, 16)  \
0                                    NaN                                NaN   
1                                    NaN                                NaN   
2                                    NaN                                NaN   
3                                    NaN                                NaN   
4                                    NaN                                NaN   
...                                  ...                                ...   
1637                                 NaN 

In [17]:
# joined_1.dtypes
from sklearn.compose import make_column_selector as selector

categorical_columns_selector = selector(dtype_include=object)
categorical_columns = categorical_columns_selector(joined_1)
categorical_columns

['Desc_Prueba',
 'Sexo',
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 0),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 1),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 2),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 3),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 4),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 5),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 6),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 7),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 8),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 9),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 10),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 11),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 12),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 13),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 14),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 15),
 ('Cantidad de Sat', Timedelta('0 days 00:00:00'), 16),
 ('Cantidad de Sat', Timedelta('0